In [1]:
import time
import concurrent
from concurrent import futures
from typing import Any, List, Dict, Tuple

from PIL import Image
from openai import AzureOpenAI
from tqdm.auto import tqdm

import json
from pathlib import Path

import pandas as pd
import requests
from dotenv import dotenv_values
from smolagents import tool, DuckDuckGoSearchTool
import wikipediaapi



test_api_base = "https://agents-course-unit4-scoring.hf.space"

def get_random_question():
    url = f"{test_api_base}/random-question"


    try:
        # Fetch the random question
        response = requests.get(url, timeout=10)
        response.raise_for_status()
        question_data = response.json()

        # Check if there's an associated file to download
        if question_data.get("file_name") and question_data.get("task_id"):
            task_id = question_data["task_id"]
            file_url = f"{test_api_base}/files/{task_id}"

            # Create a directory for downloaded files if it doesn't exist
            download_dir = Path("downloaded_files")
            download_dir.mkdir(exist_ok=True)

            # Download the file
            file_response = requests.get(file_url, timeout=30)
            file_response.raise_for_status()

            # Get filename from content-disposition header or use task_id
            content_disposition = file_response.headers.get('content-disposition', '')
            filename = content_disposition.split('filename=')[1].strip('"')
            file_path = download_dir / filename

            # Save the file
            with open(file_path, 'wb') as f:
                f.write(file_response.content)

            # Add the file path to the question data
            question_data['downloaded_file_path'] = str(file_path)
            print(f"Downloaded file to: {file_path}")

        return question_data

    except requests.exceptions.RequestException as e:
        print(f"Error fetching question: {e}")
        return None
    except json.JSONDecodeError as e:
        print(f"Error parsing JSON response: {e}")
        return None
    except Exception as e:
        print(f"Unexpected error: {e}")
        return None

/Users/vladi/miniconda3/envs/gaia/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
question = get_random_question()
if question:
    print(f"Task ID: {question.get('task_id')}")
    print(f"Question: {question.get('question')}")
    print(f"Level: {question.get('Level')}")
    if 'downloaded_file_path' in question:
        print(f"Downloaded file: {question['downloaded_file_path']}")

Downloaded file to: downloaded_files/99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3.mp3
Task ID: 99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3
Question: Hi, I'm making a pie but I could use some help with my shopping list. I have everything I need for the crust, but I'm not sure about the filling. I got the recipe from my friend Aditi, but she left it as a voice memo and the speaker on my phone is buzzing so I can't quite make out what she's saying. Could you please listen to the recipe and list all of the ingredients that my friend described? I only want the ingredients for the filling, as I have everything I need to make my favorite pie crust. I've attached the recipe as Strawberry pie.mp3.

In your response, please only list the ingredients, not any measurements. So if the recipe calls for "a pinch of salt" or "two cups of ripe strawberries" the ingredients on the list would be "salt" and "ripe strawberries".

Please format your response as a comma separated list of ingredients. Also, please alphabeti

In [3]:
config = dotenv_values()

client = AzureOpenAI(
    api_key=config["AZURE_OPENAI_API_KEY"],
    azure_endpoint=config["AZURE_OPENAI_API_BASE"],
    api_version=config["AZURE_OPENAI_API_VERSION"]
)
model_id=config["AZURE_OPENAI_CHAT_MODEL"]

# Question Processing

In [4]:
response = requests.get(f"{test_api_base}/questions", timeout=15)
response.raise_for_status()

questions_data = response.json()

In [5]:
pd.DataFrame(questions_data)

task_id  \
0   8e867cd7-cff9-4e6c-867a-ff5ddc2550be   
1   a1e91b78-d3d8-4675-bb8d-62741b4b68a6   
2   2d83110e-a098-4ebb-9987-066c06fa42d0   
3   cca530fc-4052-43b2-b130-b30968d8aa44   
4   4fc2f1ae-8625-45b5-ab34-ad4433bc21f8   
5   6f37996b-2ac7-44b0-8e68-6d28256631b4   
6   9d191bce-651d-4746-be2d-7ef8ecadb9c2   
7   cabe07ed-9eca-40ea-8ead-410ef5e83f91   
8   3cef3a44-215e-4aed-8e3b-b1e3f08063b7   
9   99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3   
10  305ac316-eef6-4446-960a-92d80d542f82   
11  f918266a-b3e0-4914-865d-4faa564f1aef   
12  3f57289b-8c60-48be-bd80-01f8099ca449   
13  1f975693-876d-457b-a649-393859e79bf3   
14  840bfca7-4f7b-481a-8794-c560c340185d   
15  bda648d7-d618-4883-88f4-3466eabd860e   
16  cf106601-ab4f-4af9-b045-5295fe67b37d   
17  a0c07678-e491-4bbc-8f0b-07405144218f   
18  7bd855d8-463d-4ed5-93ca-5fe35145f733   
19  5a0c1adf-205e-4841-a666-7c3ef95def9d   

                                             question Level  \
0   How many studio albums were published by Merce...     1   
1   In the video https://www.youtube.com/watch?v=L...     1   
2   .rewsna eht sa "tfel" drow eht fo etisoppo eht...     1   
3   Review the chess position provided in the imag...     1   
4   Who nominated the only Featured Article on Eng...     1   
5   Given this table defining * on the set S = {a,...     1   
6   Examine the video at https://www.youtube.com/w...     1   
7   What is the surname of the equine veterinarian...     1   
8   I'm making a grocery list for my mom, but she'...     1   
9   Hi, I'm making a pie but I could use some help...     1   
10  Who did the actor who played Ray in the Polish...     1   
11  What is the final numeric output from the atta...     1   
12  How many at bats did the Yankee with the most ...     1   
13  Hi, I was out sick from my classes on Friday, ...     1   
14  On June 6, 2023, an article by Carolyn Collins...     1   
15  Where were the Vietnamese specimens described ...     1   
16  What country had the least number of athletes ...     1   
17  Who are the pitchers with the number before an...     1   
18  The attached Excel file contains the sales of ...     1   
19  What is the first name of the only Malko Compe...     1   

                                    file_name  
0                                              
1                                              
2                                              
3    cca530fc-4052-43b2-b130-b30968d8aa44.png  
4                                              
5                                              
6                                              
7                                              
8                                              
9    99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3.mp3  
10                                             
11    f918266a-b3e0-4914-865d-4faa564f1aef.py  
12                                             
13   1f975693-876d-457b-a649-393859e79bf3.mp3  
14                                             
15                                             
16                                             
17                                             
18  7bd855d8-463d-4ed5-93ca-5fe35145f733.xlsx  
19

In [11]:
df = pd.DataFrame(questions_data)
df[df["file_name"] == ""]["question"].values

array(['How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
       'In the video https://www.youtube.com/watch?v=L1vXCYZAYYM, what is the highest number of bird species to be on camera simultaneously?',
       '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI',
       'Who nominated the only Featured Article on English Wikipedia about a dinosaur that was promoted in November 2016?',
       'Given this table defining * on the set S = {a, b, c, d, e}\n\n|*|a|b|c|d|e|\n|---|---|---|---|---|---|\n|a|a|b|c|b|d|\n|b|b|c|a|e|c|\n|c|c|a|b|b|a|\n|d|b|e|b|e|d|\n|e|d|b|a|d|c|\n\nprovide the subset of S involved in any possible counter-examples that prove * is not commutative. Provide your answer as a comma separated list of the elements in the set in alphabetical order.',
       'Examine the video at https://www.youtube.com/watch?v=1htKBjuUWec.\n\nWhat does Teal\'c

In [28]:
@tool
def read_file(file_path_str: str) -> str:
    """
    A tool that reads the contents of a file and returns them as text.

    Args:
        file_path_str: The path to the file that should be read.
    """

    file_path = Path(file_path_str)
    file_path = file_path.resolve()
    if not file_path.exists() or not file_path.is_file():
        raise ValueError(f"File {file_path} does not exist or is not a file.")

    switcher = {
        ".txt": lambda: file_path.read_text(encoding="utf-8"),
        ".csv": lambda: file_path.read_text(encoding="utf-8"),
        ".py": lambda: file_path.read_text(encoding="utf-8"),
        ".xlsx": lambda: pd.read_excel(file_path).to_string(),
    }

    return switcher.get(file_path.suffix, lambda: "Unsupported file type")()

@tool
def wikipedia_search(page: str) -> str:
    """
    A tool that returns the contents for a specific Wikipedia page if found, or "This content has been truncated to stay below 0 characters" if page not found.

    Args:
        page: The Wikipedia page for which to retrieve the content.
    """
    wiki_wiki = wikipediaapi.Wikipedia(user_agent='LLM Agents', language='en')

    page_py = wiki_wiki.page(page)
    return page_py.text

def process_question(question_data: dict[str, Any]) -> dict[str, str]:
    task_id = question_data.get("task_id")
    question_text = question_data.get("question")
    format_instructions = "You are a general AI assistant. I will ask you a question. Report your thoughts, and finish your answer with the following template: FINAL ANSWER: [YOUR FINAL ANSWER]. YOUR FINAL ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings. If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. If you are asked for a string, don't use articles, neither abbreviations (e.g. for cities), and write the digits in plain text unless specified otherwise. If you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string."
    adjusted_question_text = f"{format_instructions}\n\n{question_text}"

    file_path = None
    if question_data.get("file_name"):
        task_id = question_data["task_id"]
        file_url = f"{test_api_base}/files/{task_id}"

        download_dir = Path("downloaded_files")
        download_dir.mkdir(exist_ok=True)

        file_response = requests.get(file_url, timeout=30)
        file_response.raise_for_status()

        file_path = download_dir / question_data.get("file_name")

        with open(file_path, 'wb') as f:
            f.write(file_response.content)

    agent = CodeAgent(tools=[read_file,
                             # wikipedia_search
                                DuckDuckGoSearchTool(),
                                VisitWebpageTool()
                             ], model=model, max_steps=10,
                      # verbosity_level=0,
                      max_print_outputs_length=0)

    if file_path and file_path.suffix in ['.png', '.jpg', '.jpeg']:   # I know, it's inconsistent
        answer = agent.run(task=adjusted_question_text, images=[Image.open(file_path)])
    else:
        answer = agent.run(task=f"{adjusted_question_text}{f' File: |{file_path}|' if question_data.get('file_name') else ''}", )

    # print(f"Task ID: {task_id}, Question: {question_text}, Answer: {answer}")

    return {
        "task_id": task_id,
        "submitted_answer": answer,
        "question": question_text
    }


def run_agents_parallel(questions_data: List[Dict[str, Any]], max_workers: int = 4) -> Tuple[Dict[str, Any], List[Dict[str, Any]]]:
    start = time.time()

    answers = []
    results_log = []

    with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
        future_to_question = {executor.submit(process_question, q): q for q in questions_data}

        for future in tqdm(concurrent.futures.as_completed(future_to_question)):
            try:
                answer = future.result()
                results_log.append(answer)
                answers.append(answer)

            except Exception as e:
                print(f"Question processing failed: {e}")

    submission_data = {
        "username": "vladi",
        "agent_code": "https://huggingface.co/spaces/vladi/AgentsGAIAFun",
        "answers": answers
    }
    end = time.time()
    print(f"Processing time (parallel): {end - start:.2f} seconds")

    return submission_data, results_log

def run_agents(questions_data: list[{}]):
    start = time.time()

    answers = []
    results_log = []
    for question_data in tqdm(questions_data):

        answer = process_question(question_data)

        results_log.append(answer)
        answers.append(answer)

    submission_data = {
        "username": "vladi",
        "agent_code": "https://huggingface.co/spaces/vladi/AgentsGAIAFun",
        "answers": answers
    }

    end = time.time()
    print(f"Processing time (sequential): {end - start:.2f} seconds")

    return submission_data, results_log

def submit_answers(submission_data: dict):
    print(f"Submitting {len(submission_data['answers'])} answers")

    response = requests.post(f"{test_api_base}/submit", json=submission_data, timeout=60)
    response.raise_for_status()
    result_data = response.json()

    return result_data


In [ ]:
submission_data, results_log = run_agents(questions_data[:1])
# submission_data, results_log = run_agents_parallel(questions_data)
results_df = pd.DataFrame(results_log)

results_log

In [9]:
submission_data

{'username': 'vladi',
 'agent_code': 'https://huggingface.co/spaces/vladi/AgentsGAIAFun',
 'answers': [{'task_id': '2d83110e-a098-4ebb-9987-066c06fa42d0',
   'submitted_answer': 'right',
   'question': '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI'},
  {'task_id': 'a1e91b78-d3d8-4675-bb8d-62741b4b68a6',
   'submitted_answer': 'I lack tools for video analysis. This task requires external video analysis tools or manual review.',
   'question': 'In the video https://www.youtube.com/watch?v=L1vXCYZAYYM, what is the highest number of bird species to be on camera simultaneously?'},
  {'task_id': 'cca530fc-4052-43b2-b130-b30968d8aa44',
   'submitted_answer': 'Nd2',
   'question': "Review the chess position provided in the image. It is black's turn. Provide the correct next move for black which guarantees a win. Please provide your response in algebraic notation."},
  {'task_id': '6f37996b-2ac7-44b0-8e68-6d28256631b4',
   'submitted_answer': 'b,e',
   '

In [10]:
submit_answers(submission_data)

Submitting 19 answers


{'username': 'vladi',
 'score': 10.0,
 'correct_count': 2,
 'total_attempted': 19,
 'message': 'Score calculated successfully: 2/20 total questions answered correctly (19 valid tasks attempted). Score did not improve previous record, leaderboard not updated.',
 'timestamp': '2025-05-01T14:53:15.124360+00:00'}

In [27]:
wikipedia_search("Mercedes Sosa")

'Haydée Mercedes "La Negra" Sosa (Latin American Spanish: [meɾˈseðes ˈsosa]; 9 July 1935 – 4 October 2009) was an Argentine singer who was popular throughout Latin America and many countries outside the region. With her roots in Argentine folk music, Sosa became one of the preeminent exponents of El nuevo cancionero. She gave voice to songs written by many Latin American songwriters. Her music made people hail her as the "voice of the voiceless ones". She was often called "the conscience of Latin America".\nSosa performed in venues such as the Lincoln Center in New York City, the Théâtre Mogador in Paris, the Sistine Chapel in Vatican City, as well as sold-out shows in New York\'s Carnegie Hall and the Roman Colosseum during her final decade of life. Her career spanned four decades and she was the recipient of six Latin Grammy awards (2000, 2003, 2004, 2006, 2009, 2011), including a Latin Grammy Lifetime Achievement Award in 2004 and two posthumous Latin Grammy Award for Best Folk Albu